In [4]:
%%writefile lab/gpu_practice1.cpp
#include <CL/sycl.hpp>
#include <iostream>
#include <vector>
#include <thread>
#include <chrono>

using namespace std;
using namespace sycl;

// Función secuencial de multiplicación de matrices
void matrix_multiply_sequential(const std::vector<float>& A, const std::vector<float>& B, 
                                std::vector<float>& C, size_t N) {
    for (size_t i = 0; i < N; i++) {
        for (size_t j = 0; j < N; j++) {
            float sum = 0;
            for (size_t k = 0; k < N; k++) {
                sum += A[i * N + k] * B[k * N + j];
            }
            C[i * N + j] = sum;
        }
    }
}

// Función paralela de multiplicación de matrices con SYCL
void matrix_multiply_parallel(const std::vector<float>& A, const std::vector<float>& B, 
                              std::vector<float>& C, size_t N, queue& q) {
    buffer a_buf(A.data(), range<1>(N * N));
    buffer b_buf(B.data(), range<1>(N * N));
    buffer c_buf(C.data(), range<1>(N * N));

    q.submit([&](handler& h) {
        auto a = a_buf.get_access<access::mode::read>(h);
        auto b = b_buf.get_access<access::mode::read>(h);
        auto c = c_buf.get_access<access::mode::write>(h);

        h.parallel_for(range<2>(N, N), [=](id<2> idx) {
            size_t row = idx[0];
            size_t col = idx[1];
            float sum = 0;

            for (size_t k = 0; k < N; k++) {
                sum += a[row * N + k] * b[k * N + col];
            }
            c[row * N + col] = sum;
        });
    });

    q.wait(); // Sincroniza las operaciones
}

// Función para imprimir matrices
void print_matrix(const std::vector<float>& matrix, size_t N) {
    for (size_t i = 0; i < N; ++i) {
        for (size_t j = 0; j < N; ++j) {
            std::cout << matrix[i * N + j] << " ";
        }
        std::cout << std::endl;
    }
}

int main() {
    const size_t N = 4; // Tamaño de la matriz (NxN)
    std::vector<float> A(N * N, 1.0); // Inicializa con 1s
    std::vector<float> B(N * N, 2.0); // Inicializa con 2s
    std::vector<float> C(N * N, 0.0); // Resultado

    // Crear una cola SYCL para la CPU
    queue cpu_queue{sycl::cpu_selector_v};
    std::cout << "\nUsando dispositivo (CPU): " << cpu_queue.get_device().get_info<info::device::name>() << "\n";

    // Crear una cola SYCL para la GPU
    queue gpu_queue{sycl::gpu_selector_v};
    std::cout << "Usando dispositivo (GPU): " << gpu_queue.get_device().get_info<info::device::name>() << "\n\n";

    // ========================================
    // Multiplicación secuencial (en la CPU)
    // ========================================
    auto start = chrono::high_resolution_clock::now();
    matrix_multiply_sequential(A, B, C, N);  // Multiplicación secuencial (CPU)
    auto end = chrono::high_resolution_clock::now();
    chrono::duration<double> secuential_duration = end - start;
    cout << "Tiempo de ejecución secuencial (CPU): " << secuential_duration.count() << " segundos.\n";

    cout << "Resultado de la multiplicación secuencial (CPU):\n";
    print_matrix(C, N);
    cout << "\n";

    // Resetear la matriz C para el cálculo paralelo
    fill(C.begin(), C.end(), 0.0);

    // ========================================
    // Multiplicación paralela en GPU
    // ========================================
    start = chrono::high_resolution_clock::now();

    // Ejecutar en paralelo en la GPU
    matrix_multiply_parallel(A, B, C, N, gpu_queue);

    end = chrono::high_resolution_clock::now();
    chrono::duration<double> gpu_duration = end - start;
    cout << "Tiempo de ejecución paralelo (GPU): " << gpu_duration.count() << " segundos.\n";

    cout << "Resultado de la multiplicación paralela (GPU):\n";
    print_matrix(C, N);
    cout << "\n";

    // Resetear la matriz C para el cálculo paralelo en CPU
    fill(C.begin(), C.end(), 0.0);

    // ========================================
    // Multiplicación paralela en CPU
    // ========================================
    start = chrono::high_resolution_clock::now();

    // Ejecutar en paralelo en la CPU
    matrix_multiply_parallel(A, B, C, N, cpu_queue);

    end = chrono::high_resolution_clock::now();
    chrono::duration<double> cpu_duration = end - start;
    cout << "Tiempo de ejecución paralelo (CPU): " << cpu_duration.count() << " segundos.\n";

    cout << "Resultado de la multiplicación paralela (CPU):\n";
    print_matrix(C, N);
    cout << "\n";

    return 0;
}


Overwriting lab/gpu_practice1.cpp


In [6]:
! chmod 755 run_gpu1.sh
! if [ -x "$(command -v sbatch)" ]; then sbatch run_gpu1.sh; else ./run_gpu1.sh; fi

sbatch: error: AssocMaxSubmitJobLimit
sbatch: error: Batch job submission failed: Job violates accounting/QOS policy (job submit limit, user's size and/or time limits)


In [2]:
!squeue

             JOBID PARTITION     NAME     USER ST       TIME  NODES NODELIST(REASON)
             12780   GaudiVM 06-spawn uc0c31c8  R      18:45      1 idc-training-gaudi-compute-01
             12781  pvc-free 04-spawn u824c726  R       9:50      1 idc-training-gpu-compute-29
             12779  pvc-free 07-spawn ucb3172e  R      21:56      1 idc-training-gpu-compute-30
             12778  pvc-free 07-spawn ub1c26ad  R      29:57      1 idc-training-gpu-compute-28
             12777  pvc-free 06-spawn u0068f82  R      33:57      1 idc-training-gpu-compute-30
             12776  pvc-free 05-spawn u5be281d  R      45:40      1 idc-training-gpu-compute-27
             12775  pvc-free 06-spawn u212832f  R      51:11      1 idc-training-gpu-compute-28
             12773  pvc-free 04-spawn u90d0ae4  R      53:25      1 idc-training-gpu-compute-27
             12782 pvc-share run_gpu1 u0068f82  R       0:03      1 idc-training-gpu-compute-05
             12770 pvc-share 04-spawn u22cdf0b  R

In [3]:
!squeue -u $(whoami)

             JOBID PARTITION     NAME     USER ST       TIME  NODES NODELIST(REASON)
             12777  pvc-free 06-spawn u0068f82  R      34:02      1 idc-training-gpu-compute-30
             12782 pvc-share run_gpu1 u0068f82  R       0:08      1 idc-training-gpu-compute-05


In [3]:
! chmod 755 q.sh

In [20]:
! chmod 755 q.sh; chmod 755 run_gpu1.sh;if [ -x "$(command -v qsub)" ]; then ./q.sh run_gpu1.sh; else ./run_gpu1.sh; fi

## u0068f821c48e34a98dc6c80a500121f Se está compilando la multiplicacion de matrices en paralelo, en simultaneo Gpu y Cpu - gpu_practice1.cpp

Usando dispositivo (CPU): Intel(R) Xeon(R) Platinum 8468V
Usando dispositivo (GPU): Intel(R) Data Center GPU Max 1100

Tiempo de ejecución secuencial (CPU): 0.120713 segundos.
Resultado de la multiplicación secuencial (CPU):
1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 10

In [16]:
!icpx -o gpu_practice1 lab/gpu_practice1.cpp -fsycl

In [11]:
!./q.sh run_gpu1.sh

✅ Script detectado: run_gpu1.sh
📤 Enviando trabajo al Intel(R) DevCloud...

🧹 Limpiando archivos de salida antiguos...
📜 Subiendo el trabajo con qsub...
./q.sh: line 30: qsub: command not found
🆔 Trabajo enviado. Job ID: 

🔍 Estado inicial del trabajo:
./q.sh: line 37: qstat: command not found

⏳ Esperando la salida del trabajo ██████████████████████████████████████████████████████████████████████
⚠️ Tiempo de espera agotado: El trabajo aún está en cola o ejecutándose.
   Revisa más tarde el archivo de salida: run_gpu1.sh.o

🧹 Limpiando archivos generados por qsub...
🧹 Limpieza completada.


In [12]:
!./gpu_practice1 output1.txt


Usando dispositivo (CPU): Intel(R) Xeon(R) Platinum 8468V
Usando dispositivo (GPU): Intel(R) Data Center GPU Max 1100

Tiempo de ejecución secuencial (CPU): 4.25e-07 segundos.
Resultado de la multiplicación secuencial (CPU):
16 16 16 16 16 16 16 16 
16 16 16 16 16 16 16 16 
16 16 16 16 16 16 16 16 
16 16 16 16 16 16 16 16 
16 16 16 16 16 16 16 16 
16 16 16 16 16 16 16 16 
16 16 16 16 16 16 16 16 
16 16 16 16 16 16 16 16 

Tiempo de ejecución paralelo (GPU): 0.106184 segundos.
Resultado de la multiplicación paralela (GPU):
16 16 16 16 16 16 16 16 
16 16 16 16 16 16 16 16 
16 16 16 16 16 16 16 16 
16 16 16 16 16 16 16 16 
16 16 16 16 16 16 16 16 
16 16 16 16 16 16 16 16 
16 16 16 16 16 16 16 16 
16 16 16 16 16 16 16 16 

Tiempo de ejecución paralelo (CPU): 0.155603 segundos.
Resultado de la multiplicación paralela (CPU):
16 16 16 16 16 16 16 16 
16 16 16 16 16 16 16 16 
16 16 16 16 16 16 16 16 
16 16 16 16 16 16 16 16 
16 16 16 16 16 16 16 16 
16 16 16 16 16 16 16 16 
16 16 16 16 16 16 

In [18]:
!./gpu_practice1 output1.txt


Usando dispositivo (CPU): Intel(R) Xeon(R) Platinum 8468V
Usando dispositivo (GPU): Intel(R) Data Center GPU Max 1100

Tiempo de ejecución secuencial (CPU): 5.57302 segundos.
Resultado de la multiplicación secuencial (CPU):
2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [19]:
! chmod 755 q.sh; chmod 755 run_gpu1.sh;if [ -x "$(command -v qsub)" ]; then ./q.sh run_gpu1.sh; else ./run_gpu1.sh; fi

## u0068f821c48e34a98dc6c80a500121f Se está compilando la multiplicacion de matrices en paralelo, en simultaneo Gpu y Cpu - gpu_practice1.cpp

Usando dispositivo (CPU): Intel(R) Xeon(R) Platinum 8468V
Usando dispositivo (GPU): Intel(R) Data Center GPU Max 1100

Tiempo de ejecución secuencial (CPU): 0.120845 segundos.
Resultado de la multiplicación secuencial (CPU):
1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 1024 10

In [21]:
! chmod 755 q.sh; chmod 755 run_gpu1.sh;if [ -x "$(command -v qsub)" ]; then ./q.sh run_gpu1.sh; else ./run_gpu1.sh; fi

## u0068f821c48e34a98dc6c80a500121f Se está compilando la multiplicacion de matrices en paralelo, en simultaneo Gpu y Cpu - gpu_practice1.cpp

Usando dispositivo (CPU): Intel(R) Xeon(R) Platinum 8468V
Usando dispositivo (GPU): Intel(R) Data Center GPU Max 1100

Tiempo de ejecución secuencial (CPU): 5.86387 segundos.
Resultado de la multiplicación secuencial (CPU):
2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 2048 204

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)

